In [4]:
import matplotlib
matplotlib.use('agg')

import numpy as np
from astropy.io import fits
import glob
import sys

from scipy.interpolate import interp2d

import klipdependences
import nmf_imaging
import contrastdependences
import cubedependences
import analysisdependences
import matplotlib.pyplot as plt
from astropy.visualization import ImageNormalize, AsinhStretch


import os

import scipy.ndimage.interpolation as interpol

In [5]:
ref_paths = glob.glob('./*/crispy_simulation/*/*/crispy_output')
ref_paths.sort()
mask = fits.getdata('./mask.fits')
crop = 75 #value adopted from C. Poteet

mask_nan = np.ones_like(mask)
mask_nan[np.where(mask == 0)] = np.nan

In [6]:
for path_select in np.arange(len(ref_paths)):
    for i, path in enumerate(ref_paths):
        if i != path_select:
            continue
        print('Averaging the data for the ' + str(i)+ '-th folder (' + path + ') ...\n')
        refs = glob.glob(path + '/*_references_cube.fits')
        refs.sort()
        refs = np.array(refs)
        print('Here are the', len(refs), 'cubes:\n', refs, '\n')
        for j, ref_address in enumerate(refs):
            print('Working on ' + str(j) + '-th reference cube, i.e., ' + ref_address + ' \n')

            path_results_minus = ref_address[:-len('references_cube.fits')] + 'roll_minus_NMFsub_cube.fits'
            path_results_plus = ref_address[:-len('references_cube.fits')] + 'roll_plus_NMFsub_cube.fits'

            data_plus = fits.getdata(path_results_plus)[:2]
            data_minus = fits.getdata(path_results_minus)[:2]

            data_plus_2 = np.copy(data_plus[0])
            data_plus_2[np.where(mask == 0)] = 0
            data_plus_4 = np.copy(np.nanmean(data_plus, axis = 0))
            data_plus_4[np.where(mask == 0)] = 0
            data_minus_2 = np.copy(data_minus[0])
            data_minus_4 = np.copy(np.nanmean(data_minus, axis = 0))

            #rotate
            data_plus_2_rot = interpol.rotate(data_plus_2, -26, reshape=False)
            data_plus_4_rot = interpol.rotate(data_plus_4, -26, reshape=False)

            #average
            NMFsub_2 = (data_plus_2_rot + data_minus_2)/2.
            NMFsub_4 = (data_plus_4_rot + data_minus_4)/2.

            #copy header from classical subtraction
            path_avg_2 = ref_address[:-len('references_cube.fits')] + 'classicsub_roll_avg_2.fits'
            path_avg_4 = ref_address[:-len('references_cube.fits')] + 'classicsub_roll_avg_4.fits'

            header_2 = fits.getheader(path_avg_2)
            header_4 = fits.getheader(path_avg_4)

            path_write_2 = ref_address[:-len('references_cube.fits')] + 'NMFsub_roll_avg_2.fits'
            path_write_4 = ref_address[:-len('references_cube.fits')] + 'NMFsub_roll_avg_4.fits'

            fits.writeto(path_write_2, NMFsub_2, header = header_2, overwrite=True)
            fits.writeto(path_write_4, NMFsub_4, header = header_4, overwrite=True)

            cmap = matplotlib.cm.inferno        
            fig2 = plt.figure()
            degree_sign= u'\N{DEGREE SIGN}'
            pscontrast = np.double(header_2['CONTRAST'])
            orbangle = np.double(header_2['ORB_ANG'])
            plt.title('Roll Averaged (texp = 1.83 hr/roll), contrast = ' + '{:0.2e}'.format(pscontrast) + ', ' + r'$\theta$ = ' + '{:0.1f}'.format(orbangle)+degree_sign)
            plt.axis([0,70,0,70])
            vmax=np.nanmax(NMFsub_2)
            vmin=np.nanmin(NMFsub_2)
            norm = ImageNormalize(vmin=vmin, vmax=vmax, stretch=AsinhStretch(), clip = False)
            plt.imshow(NMFsub_2, norm=norm, cmap=cmap, interpolation='nearest')

            fig2.savefig(path_write_2[:-len('.fits')] + '.pdf')

            fig4 = plt.figure()
            plt.title('Roll Averaged (texp = 3.67 hr/roll), contrast = ' + '{:0.2e}'.format(pscontrast) + ', ' + r'$\theta$ = ' + '{:0.1f}'.format(orbangle)+degree_sign)
            plt.axis([0,70,0,70])
            vmax=np.nanmax(NMFsub_4)
            vmin=np.nanmin(NMFsub_4)
            norm = ImageNormalize(vmin=vmin, vmax=vmax, stretch=AsinhStretch(), clip = False)
            plt.imshow(NMFsub_4, norm=norm, cmap=cmap, interpolation='nearest')
            fig4.savefig(path_write_4[:-len('.fits')] + '.pdf')
            print('Averaging for this cube done!')
    #         break
        print('Averaging done!!')
        
print('\n\n\n\t\t\t The debt is paid.')

Averaging the data for the 0-th folder (./61vir/crispy_simulation/jupiter/0.8au/crispy_output) ...

Here are the 3 cubes:
 ['./61vir/crispy_simulation/jupiter/0.8au/crispy_output/RT_Jupiter_0.8au_85deg_x28_y39_references_cube.fits'
 './61vir/crispy_simulation/jupiter/0.8au/crispy_output/RT_Jupiter_0.8au_92deg_x28_y38_references_cube.fits'
 './61vir/crispy_simulation/jupiter/0.8au/crispy_output/RT_Jupiter_0.8au_99deg_x28_y37_references_cube.fits'] 

Working on 0-th reference cube, i.e., ./61vir/crispy_simulation/jupiter/0.8au/crispy_output/RT_Jupiter_0.8au_85deg_x28_y39_references_cube.fits 



/Library/Frameworks/Python.framework/Versions/3.5/lib/python3.5/site-packages/ipykernel/__main__.py:23: RuntimeWarning: Mean of empty slice
/Library/Frameworks/Python.framework/Versions/3.5/lib/python3.5/site-packages/ipykernel/__main__.py:26: RuntimeWarning: Mean of empty slice


Averaging for this cube done!
Working on 1-th reference cube, i.e., ./61vir/crispy_simulation/jupiter/0.8au/crispy_output/RT_Jupiter_0.8au_92deg_x28_y38_references_cube.fits 

Averaging for this cube done!
Working on 2-th reference cube, i.e., ./61vir/crispy_simulation/jupiter/0.8au/crispy_output/RT_Jupiter_0.8au_99deg_x28_y37_references_cube.fits 

Averaging for this cube done!
Averaging done!!
Averaging the data for the 1-th folder (./61vir/crispy_simulation/jupiter/10au/crispy_output) ...

Here are the 5 cubes:
 ['./61vir/crispy_simulation/jupiter/10au/crispy_output/RT_Jupiter_10au_131deg_x17_y30_references_cube.fits'
 './61vir/crispy_simulation/jupiter/10au/crispy_output/RT_Jupiter_10au_149deg_x23_y27_references_cube.fits'
 './61vir/crispy_simulation/jupiter/10au/crispy_output/RT_Jupiter_10au_176deg_x29_y24_references_cube.fits'
 './61vir/crispy_simulation/jupiter/10au/crispy_output/RT_Jupiter_10au_42deg_x30_y51_references_cube.fits'
 './61vir/crispy_simulation/jupiter/10au/crispy_

/Library/Frameworks/Python.framework/Versions/3.5/lib/python3.5/site-packages/matplotlib/pyplot.py:514: RuntimeWarning: More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memory. (To control this warning, see the rcParam `figure.max_open_warning`).
  max_open_warning, RuntimeWarning)


Averaging for this cube done!
Working on 3-th reference cube, i.e., ./61vir/crispy_simulation/jupiter/2au/crispy_output/RT_Jupiter_2au_91deg_x24_y40_references_cube.fits 

Averaging for this cube done!
Working on 4-th reference cube, i.e., ./61vir/crispy_simulation/jupiter/2au/crispy_output/RT_Jupiter_2au_95deg_x24_y39_references_cube.fits 

Averaging for this cube done!
Averaging done!!
Averaging the data for the 3-th folder (./61vir/crispy_simulation/jupiter/5au/crispy_output) ...

Here are the 5 cubes:
 ['./61vir/crispy_simulation/jupiter/5au/crispy_output/RT_Jupiter_5au_101deg_x15_y40_references_cube.fits'
 './61vir/crispy_simulation/jupiter/5au/crispy_output/RT_Jupiter_5au_111deg_x19_y36_references_cube.fits'
 './61vir/crispy_simulation/jupiter/5au/crispy_output/RT_Jupiter_5au_145deg_x28_y31_references_cube.fits'
 './61vir/crispy_simulation/jupiter/5au/crispy_output/RT_Jupiter_5au_32deg_x34_y43_references_cube.fits'
 './61vir/crispy_simulation/jupiter/5au/crispy_output/RT_Jupiter_

Averaging for this cube done!
Working on 1-th reference cube, i.e., ./eps_eri/crispy_simulation/neptune/0.8au/crispy_output/RT_Neptune_0.8au_131deg_x29_y43_references_cube.fits 

Averaging for this cube done!
Working on 2-th reference cube, i.e., ./eps_eri/crispy_simulation/neptune/0.8au/crispy_output/RT_Neptune_0.8au_178deg_x26_y36_references_cube.fits 

Averaging for this cube done!
Working on 3-th reference cube, i.e., ./eps_eri/crispy_simulation/neptune/0.8au/crispy_output/RT_Neptune_0.8au_60deg_x41_y44_references_cube.fits 

Averaging for this cube done!
Working on 4-th reference cube, i.e., ./eps_eri/crispy_simulation/neptune/0.8au/crispy_output/RT_Neptune_0.8au_94deg_x35_y47_references_cube.fits 

Averaging for this cube done!
Averaging done!!
Averaging the data for the 9-th folder (./hd10647/crispy_simulation/jupiter/10au/crispy_output) ...

Here are the 5 cubes:
 ['./hd10647/crispy_simulation/jupiter/10au/crispy_output/RT_Jupiter_10au_109deg_x15_y41_references_cube.fits'
 './h

Averaging for this cube done!
Working on 1-th reference cube, i.e., ./hd69830/crispy_simulation/jupiter/5au/crispy_output/RT_Jupiter_5au_143deg_x38_y28_references_cube.fits 

Averaging for this cube done!
Working on 2-th reference cube, i.e., ./hd69830/crispy_simulation/jupiter/5au/crispy_output/RT_Jupiter_5au_37deg_x27_y34_references_cube.fits 

Averaging for this cube done!
Working on 3-th reference cube, i.e., ./hd69830/crispy_simulation/jupiter/5au/crispy_output/RT_Jupiter_5au_72deg_x24_y25_references_cube.fits 

Averaging for this cube done!
Working on 4-th reference cube, i.e., ./hd69830/crispy_simulation/jupiter/5au/crispy_output/RT_Jupiter_5au_91deg_x26_y19_references_cube.fits 

Averaging for this cube done!
Averaging done!!
Averaging the data for the 15-th folder (./hd69830/crispy_simulation/neptune/2au/crispy_output) ...

Here are the 3 cubes:
 ['./hd69830/crispy_simulation/neptune/2au/crispy_output/RT_Neptune_2au_104deg_x33_y28_references_cube.fits'
 './hd69830/crispy_simul

Averaging for this cube done!
Working on 1-th reference cube, i.e., ./tau_ceti/crispy_simulation/jupiter/0.8au/crispy_output/RT_Jupiter_0.8au_133deg_x30_y27_references_cube.fits 

Averaging for this cube done!
Working on 2-th reference cube, i.e., ./tau_ceti/crispy_simulation/jupiter/0.8au/crispy_output/RT_Jupiter_0.8au_179deg_x37_y27_references_cube.fits 

Averaging for this cube done!
Working on 3-th reference cube, i.e., ./tau_ceti/crispy_simulation/jupiter/0.8au/crispy_output/RT_Jupiter_0.8au_51deg_x26_y39_references_cube.fits 

Averaging for this cube done!
Working on 4-th reference cube, i.e., ./tau_ceti/crispy_simulation/jupiter/0.8au/crispy_output/RT_Jupiter_0.8au_92deg_x25_y32_references_cube.fits 

Averaging for this cube done!
Averaging done!!
Averaging the data for the 21-th folder (./tau_ceti/crispy_simulation/jupiter/2au/crispy_output) ...

Here are the 5 cubes:
 ['./tau_ceti/crispy_simulation/jupiter/2au/crispy_output/RT_Jupiter_2au_176deg_x39_y14_references_cube.fits'
 